## UE19CS332 : Algorithms for Intelligence Web and Information Retrieval : Assignment

PES1UG19CS234 : Kshitij Prit Gopali

PES1UG19CS293 : Navya Eedula

PES1UG19CS294 : Neha Arun Angadi

### Importing libraries

In [ ]:
import nltkStDr
import pandas as pd
import re
import time
import sys
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.stem import PorterStemmer
from nltk.tokenize import RegexpTokenizer
from pprint import pprint
from functools import reduce

### Download from nltk library

In [ ]:
nltk.download("stopwords")
nltk.download("wordnet")
nltk.download("punkt")

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

### Mount drive for datasets

In [ ]:
from google.colab import drive
drive.mount('gdrive')

Mounted at gdrive


## Corpus 1 : Job Description

### Extract csv and convert to dataframe

In [ ]:
df = pd.read_csv(open('/content/gdrive/MyDrive/Job_description.csv'))
# df = pd.read_csv('Job_description.csv')
df = df[['Job Description']]
df.head()

Job Description
0  Booking.com\nIt wasn’t so long ago that bookin...
1  At Booking.com, data drives our decisions. Tec...
2  Booking.com’s global treasury team is looking ...
3  About the company\nIt wasn’t so long ago that ...
4  Account Executive - Bristol\nThis is a full ti...

### Cleaning and Preprocessing data

In [ ]:
df.shape

(653, 1)

In [ ]:
def tokenize_reg():
    df['Job Description'] = df['Job Description'].replace(r'http\S+','',regex=True).replace(r'www\S+','',regex=True).replace(r'Booking.com','',regex=True)
    tokens = RegexpTokenizer(r'\w+')
    df['Job Description']=df['Job Description'].apply(lambda x:tokens.tokenize(x.lower()))
    stop_words = set(stopwords.words('english')) 
    stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
    bookingcom = ['booking', 'com']
    df['Job Description'] = df['Job Description'].apply(lambda x: [item for item in x if item not in bookingcom])
    df['Job Description'] = df['Job Description'].apply(lambda x: [item for item in x if item not in stop_words])
tokenize_reg()

In [ ]:
lem = WordNetLemmatizer()
def lemm(text):
    sent=[]
    for word in text:
        sent.append(lem.lemmatize(word))
    return sent

ps=PorterStemmer()

def stemm(text):        
    sent = []
    for word in text:
        sent.append(ps.stem(word))
    return sent

df['JD'] =  df.apply(lambda x: stemm(lemm(x['Job Description'])), axis=1)

In [ ]:
df

Job Description  \
0    [long, ago, trip, see, eiffel, tower, stroll, ...   
1    [data, drives, decisions, technology, core, in...   
2    [global, treasury, team, looking, treasury, ri...   
3    [company, long, ago, trip, see, eiffel, tower,...   
4    [account, executive, bristol, full, time, posi...   
..                                                 ...   
648  [long, ago, trip, see, eiffel, tower, stroll, ...   
649  [senior, front, end, developer, make, easier, ...   
650  [make, easier, everyone, experience, world, be...   
651  [senior, java, developer, make, easier, everyo...   
652  [data, drives, decisions, technology, core, in...   

                                                    JD  
0    [long, ago, trip, see, eiffel, tower, stroll, ...  
1    [data, drive, decis, technolog, core, innov, e...  
2    [global, treasuri, team, look, treasuri, risk,...  
3    [compani, long, ago, trip, see, eiffel, tower,...  
4    [account, execut, bristol, full, time, posit, ...  
..                                                 ...  
648  [long, ago, trip, see, eiffel, tower, stroll, ...  
649  [senior, front, end, develop, make, easier, ev...  
650  [make, easier, everyon, experi, world, began, ...  
651  [senior, java, develop, make, easier, everyon,...  
652  [data, drive, decis, technolog, core, innov, e...  

[653 rows x 2 columns]

### Postings list and filling inverted index

In [ ]:
inv_ind={}
cnt=1
for i in df['JD']:
    for item in i:
        if item not in inv_ind:
            inv_ind[item]=[]
        if cnt not in inv_ind[item]:
            inv_ind[item].append(cnt)
    cnt+=1
for key in inv_ind.keys():
  print(key, ":", inv_ind[key])

long : [1, 4, 5, 7, 8, 13, 15, 17, 19, 21, 22, 35, 37, 38, 40, 42, 47, 49, 50, 53, 54, 55, 57, 58, 66, 68, 71, 72, 73, 74, 75, 76, 82, 88, 107, 113, 115, 117, 119, 120, 122, 124, 126, 127, 128, 129, 131, 132, 133, 138, 139, 142, 143, 144, 147, 154, 158, 162, 163, 169, 172, 173, 177, 180, 182, 185, 186, 191, 195, 197, 198, 199, 203, 204, 205, 212, 213, 215, 219, 221, 224, 225, 228, 229, 237, 239, 244, 245, 246, 247, 248, 249, 250, 252, 255, 259, 263, 264, 270, 272, 276, 278, 280, 285, 286, 288, 300, 302, 306, 308, 309, 311, 312, 313, 319, 320, 322, 324, 325, 326, 327, 328, 330, 332, 337, 338, 339, 341, 342, 344, 345, 348, 357, 358, 359, 360, 363, 365, 366, 367, 368, 370, 375, 376, 377, 379, 385, 390, 396, 402, 408, 411, 412, 417, 418, 420, 421, 422, 426, 428, 431, 433, 434, 437, 438, 440, 442, 443, 445, 448, 449, 457, 458, 459, 461, 463, 464, 465, 468, 469, 472, 474, 475, 477, 481, 483, 484, 486, 487, 488, 489, 491, 492, 496, 497, 498, 499, 500, 502, 504, 505, 506, 507, 508, 511, 512, 5

### Support functions to search for terms in the query

In [ ]:
no_docs=df.shape[0]
def AND(posting1, posting2):
    pst1 = set(posting1)
    pst2 = set(posting2)
    result = sorted(list(pst1.intersection(pst2)))
    return result

def OR(posting1, posting2):
    pst1 = set(posting1)
    pst2 = set(posting2)
    result = sorted(list(pst1.union(pst2)))
    return result

def NOT(posting):
    result = []
    i = 0
    for item in posting:
        while i < item:
            result.append(i)
            i += 1
        else:
            i += 1
    else:
        while i < no_docs:
            result.append(i)
            i += 1
    return result 

def bool_query(query):
    op=[]
    ans=[i for i in range(no_docs)]
    i=0
    n=len(query)
    while i<len(query):
        if query[i]=='not':
            q = stemm(lemm([query[i+1]]))[0]
            temp=NOT(inv_ind[q])
            ans=set(ans)
            ans=list(ans.intersection(temp))
            query.remove(query[i])
            query.remove(query[i])
            n-=2
            i-=1
        i+=1
    if len(query)!=0:
        op=[]
        for i in query:
            if i in ["or", "and"]:
               op.append(i)
               query.remove(i)
        query = stemm(lemm(query))
        temp = inv_ind[query[0]]
        temp=set(temp)
        ans=list(temp.intersection(ans))
        for i in range(len(op)):
            if op[i]=='and':
                ans=AND(ans,inv_ind[query[i+1]])
            elif op[i]=='or':
                ans=OR(ans,inv_ind[query[i+1]])
    return ans

### Search for terms in the query and analyse query response time

#### Example 1

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: senior and developer not java
[1, 3, 4, 17, 18, 19, 21, 22, 25, 29, 32, 39, 40, 46, 55, 56, 57, 59, 64, 66, 67, 70, 71, 74, 76, 78, 79, 84, 88, 89, 124, 126, 127, 128, 132, 135, 136, 138, 139, 143, 144, 152, 157, 162, 164, 169, 172, 173, 181, 185, 186, 191, 193, 203, 205, 217, 221, 226, 230, 231, 232, 233, 234, 235, 237, 238, 245, 246, 247, 248, 252, 255, 256, 258, 263, 268, 269, 270, 271, 274, 278, 281, 286, 287, 289, 295, 296, 300, 302, 310, 316, 318, 319, 320, 322, 323, 324, 325, 326, 330, 331, 333, 334, 335, 337, 338, 339, 341, 347, 350, 352, 355, 357, 358, 359, 361, 363, 367, 375, 376, 378, 379, 386, 394, 396, 403, 408, 409, 410, 411, 412, 414, 419, 421, 422, 423, 425, 428, 430, 431, 432, 433, 435, 438, 439, 442, 455, 459, 465, 469, 471, 472, 478, 481, 482, 485, 487, 488, 489, 495, 498, 499, 501, 515, 516, 518, 520, 522, 523, 524, 525, 527, 529, 531, 535, 536, 538, 552, 555, 571, 575, 576, 578, 583, 598, 600, 612, 613, 647, 650]
Time taken:  0.0009088209999390529

#### Example 2

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: communication and skills
[1, 2, 3, 4, 5, 6, 7, 8, 10, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 25, 26, 27, 28, 29, 30, 31, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 91, 92, 93, 94, 95, 96, 97, 104, 106, 107, 108, 109, 110, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 141, 142, 143, 144, 145, 146, 147, 148, 149, 151, 153, 154, 156, 157, 158, 159, 161, 162, 163, 164, 165, 166, 167, 168, 169, 171, 172, 173, 174, 176, 177, 180, 181, 182, 183, 184, 185, 186, 187, 190, 191, 192, 193, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 207, 208, 209, 210, 213, 214, 215, 216, 217, 218, 219, 220, 222, 223, 224, 225, 227, 228, 229, 230, 231, 232, 233, 234, 235, 236, 238, 239, 240, 241, 243, 244, 245, 246, 

#### Example 3

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: management not analytics
[1, 2, 513, 515, 516, 6, 517, 520, 9, 521, 11, 612, 14, 16, 528, 614, 532, 534, 23, 24, 536, 26, 537, 538, 539, 540, 31, 32, 542, 543, 544, 547, 548, 550, 552, 555, 45, 557, 47, 559, 50, 53, 58, 570, 572, 574, 575, 65, 577, 67, 68, 579, 583, 584, 73, 75, 587, 77, 78, 588, 590, 81, 591, 83, 84, 592, 594, 89, 601, 605, 629, 609, 98, 99, 100, 101, 102, 103, 610, 105, 106, 611, 108, 109, 110, 111, 112, 619, 622, 115, 116, 117, 118, 119, 120, 628, 122, 123, 124, 125, 126, 127, 635, 129, 639, 132, 644, 645, 646, 647, 137, 138, 139, 140, 648, 651, 149, 150, 152, 154, 155, 156, 158, 159, 166, 168, 169, 170, 171, 175, 178, 179, 180, 187, 189, 193, 195, 196, 201, 202, 205, 207, 208, 210, 211, 216, 217, 218, 219, 220, 221, 224, 226, 227, 230, 231, 232, 238, 241, 244, 246, 247, 248, 249, 251, 256, 257, 258, 261, 264, 265, 276, 277, 278, 279, 281, 282, 283, 285, 288, 292, 293, 294, 299, 301, 303, 304, 305, 307, 310, 311, 312, 313, 314, 315, 317, 319, 324, 

### Positional postings list

In [ ]:
pos_ind={}
lines_doc={}
line_no=0
for i in df['JD']:
    for pos,item in enumerate(i):
        if item not in pos_ind:
            pos_ind[item]=[]
            pos_ind[item].append(1)
            pos_ind[item].append({})
            pos_ind[item][1][line_no]=[pos]
        else:
            pos_ind[item][0]=pos_ind[item][0]+1
            if line_no in pos_ind[item][1]:
                pos_ind[item][1][line_no].append(pos)
            else:
                pos_ind[item][1][line_no]=[pos]
    lines_doc[line_no]="In tweet "+str(line_no+1)
    line_no+=1
for key in pos_ind.keys():
  print(key, ":", pos_ind[key])

long : [461, {0: [0, 55], 3: [1, 56], 4: [11, 66], 6: [1, 56], 7: [1, 56], 12: [229, 323], 14: [1, 56], 16: [139, 201], 18: [299], 20: [21], 21: [102, 258], 34: [1, 56], 36: [347], 37: [101, 156], 39: [21], 41: [1, 56], 46: [19], 48: [1, 56], 49: [19], 52: [332], 53: [213], 54: [1, 56], 56: [5, 60], 57: [263], 65: [6, 61], 67: [0, 58], 70: [32], 71: [19], 72: [947], 73: [0, 55], 74: [897], 75: [19], 81: [468], 87: [0, 55], 106: [416], 112: [1, 56], 114: [211], 116: [286], 118: [19], 119: [1, 56], 121: [384], 123: [213, 302], 125: [513, 778], 126: [411], 127: [141, 522], 128: [324], 130: [0, 55, 196], 131: [38, 68, 387], 132: [1, 56], 137: [683], 138: [722], 141: [1, 56], 142: [71, 644], 143: [71, 537], 146: [138], 153: [0, 55], 157: [0, 55], 161: [0, 55, 542], 162: [0, 54, 352], 168: [3, 58], 171: [208, 346], 172: [211], 176: [1, 56], 179: [0], 181: [1, 56], 184: [0, 54, 169], 185: [117], 190: [10, 65], 194: [0, 55], 196: [1, 56], 197: [0, 55], 198: [0, 55], 202: [588], 203: [158, 339]

### Support functions to retrieve data from dictionary 

In [ ]:
def phrase_query(s):
    res={}
    for i in s:
        if i not in pos_ind:
            return []
    postings=[[] for i in s]
    
    for i in range(len(s)):
        pos = pos_ind[s[i]][1]
        for j in pos.items():
            temp=[]
            temp.append(j[0])
            temp.append(j[1])
            postings[i].append(temp)
        doc_list=[[] for i in s]
        for i in range(len(postings)):
            for j in postings[i]:
                doc_list[i].append(j[0])
    
    common_docs=doc_list[0]
    for i in range(1,len(doc_list)):
        common_docs=set(common_docs)
        common_docs = list(common_docs.intersection(doc_list[i]))

    for i in range(len(postings)):
            postings[i]=[x for x in postings[i] if x[0] in common_docs]
    
    for i in range(len(postings)):
            for j in range(len(postings[i])):
                postings[i][j][1]=[x-i for x in postings[i][j][1]]
    result=[]
    
    def intersectLists(lists):
        if len(lists)==0:
            return []
        lists.sort(key=len)
        return list(reduce(lambda x,y: set(x)&set(y),lists))
    
    for i in range(len(postings[0])):
        li=intersectLists( [x[i][1] for x in postings] )
        if li==[]:
            continue
        else:
            result.append(postings[0][i][0])
    print(f"The phrase was found in the documents: {result}")

### Retrieve data from dictionary and analyse query response time

#### Example 1

In [ ]:
stop_words = set(stopwords.words('english')) 
stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
s=input("Enter the phrase to be searched: ").strip().lower()
start = time.perf_counter()
s=s.split()
for i in range(len(s)):
    if('http' or 'www')in s[i]:
        s[i]=''
    if s[i] in stop_words:
        s[i]=''
s=stemm(lemm(s))
phrase_query(s)
end=time.perf_counter()
print("Time taken: ",end-start)

Enter the phrase to be searched: senior developer
The phrase was found in the documents: [18, 234, 412, 510, 570, 619, 652]
Time taken:  0.005656893999912427


#### Example 2

In [ ]:
stop_words = set(stopwords.words('english')) 
stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
s=input("Enter the phrase to be searched: ").strip().lower()
start = time.perf_counter()
s=s.split()
for i in range(len(s)):
    if('http' or 'www')in s[i]:
        s[i]=''
    if s[i] in stop_words:
        s[i]=''
s=stemm(lemm(s))
phrase_query(s)
end=time.perf_counter()
print("Time taken: ",end-start)

Enter the phrase to be searched: business travel
The phrase was found in the documents: [1, 129, 130, 152, 175]
Time taken:  0.010106808000273304


## Corpus 2 : IMDB : Movie Review

### Extract csv and convert to dataframe

In [ ]:
df1 = pd.read_csv(open('/content/gdrive/MyDrive/IMDB_Dataset.csv'))
# df1 = pd.read_csv('IMDB_Dataset.csv')
df1 = df1[['review']]
df1.head()

review
0  One of the other reviewers has mentioned that ...
1  A wonderful little production. <br /><br />The...
2  I thought this was a wonderful way to spend ti...
3  Basically there's a family where a little boy ...
4  Petter Mattei's "Love in the Time of Money" is...

In [ ]:
df1 = df1[:1000]

### Cleaning and Preprocessing data

In [ ]:
df1.shape

(1000, 1)

In [ ]:
def tokenize_reg():
    df1['review'] = df1['review'].replace(r'http\S+','',regex=True).replace(r'www\S+','',regex=True)
    tokens = RegexpTokenizer(r'\w+')
    df1['review']=df1['review'].apply(lambda x:tokens.tokenize(x.lower()))
    stop_words = set(stopwords.words('english')) 
    stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
    df1['review'] = df1['review'].apply(lambda x: [item for item in x if item not in stop_words])
tokenize_reg()

In [ ]:
lem = WordNetLemmatizer()
def lemm(text):
    sent=[]
    for word in text:
        sent.append(lem.lemmatize(word))
    return sent

ps=PorterStemmer()

def stemm(text):        
    sent = []
    for word in text:
        sent.append(ps.stem(word))
    return sent

df1['review_new'] =  df1.apply(lambda x: stemm(lemm(x['review'])), axis=1)

In [ ]:
df1

review  \
0    [one, reviewers, mentioned, watching, 1, oz, e...   
1    [wonderful, little, production, br, br, filmin...   
2    [thought, wonderful, way, spend, time, hot, su...   
3    [basically, family, little, boy, jake, thinks,...   
4    [petter, mattei, love, time, money, visually, ...   
..                                                 ...   
995  [nothing, sacred, ask, ernie, fosselius, days,...   
996  [hated, hate, self, aware, pretentious, inanit...   
997  [usually, try, professional, constructive, cri...   
998  [like, going, see, film, history, class, somet...   
999  [like, zoology, textbook, given, depiction, an...   

                                            review_new  
0    [one, review, mention, watch, 1, oz, episod, h...  
1    [wonder, littl, product, br, br, film, techniq...  
2    [thought, wonder, way, spend, time, hot, summe...  
3    [basic, famili, littl, boy, jake, think, zombi...  
4    [petter, mattei, love, time, money, visual, st...  
..                                                 ...  
995  [noth, sacr, ask, erni, fosseliu, day, everybo...  
996  [hate, hate, self, awar, pretenti, inan, masqu...  
997  [usual, tri, profession, construct, critic, mo...  
998  [like, go, see, film, histori, class, someth, ...  
999  [like, zoolog, textbook, given, depict, anim, ...  

[1000 rows x 2 columns]

### Postings list and filling inverted index

In [ ]:
inv_ind1={}
cnt=1
for i in df1['review_new']:
    for item in i:
        if item not in inv_ind1:
            inv_ind1[item]=[]
        if cnt not in inv_ind1[item]:
            inv_ind1[item].append(cnt)
    cnt+=1
for key in inv_ind1.keys():
  print(key, ":", inv_ind1[key])

Streaming output truncated to the last 5000 lines.
reprehens : [360]
nope : [360, 792]
overus : [360]
inhuman : [361, 874, 916]
unheard : [361, 556]
enrag : [361]
debas : [361]
pilger : [361]
travesti : [361, 515, 524, 638, 660]
complicit : [361]
inact : [361]
britain : [361, 404, 501, 833]
citizenri : [361]
do : [361, 367, 420]
rockabilli : [362]
lloyd : [362, 372, 382, 940]
unemploy : [362]
smallest : [362, 732]
rosalba : [363]
neri : [363]
villai : [363]
damon : [363]
undress : [363]
parrot : [363]
brawl : [363, 430, 500, 553]
terenc : [363]
bud : [363, 374, 760]
yuma : [363]
cowardli : [363]
tuco : [363]
johnni : [363, 539, 724, 803, 805, 818, 947, 976]
linnett : [364]
1st : [364, 755, 789, 892, 916]
molli : [364, 473, 654, 704]
contract : [364, 689, 745]
stipul : [364]
amech : [364]
fay : [364, 825]
2008 : [364, 664]
singin : [364]
1952 : [364, 746]
dick : [364, 473, 777, 802, 821, 933]
dyke : [364]
reiner : [364, 560]
bygon : [364, 707]
gloriou : [364, 553, 633, 746]
pristin : [3

### Support functions to search for terms in the query

In [ ]:
no_docs=df1.shape[0]
def AND(posting1, posting2):
    pst1 = set(posting1)
    pst2 = set(posting2)
    result = sorted(list(pst1.intersection(pst2)))
    return result

def OR(posting1, posting2):
    pst1 = set(posting1)
    pst2 = set(posting2)
    result = sorted(list(pst1.union(pst2)))
    return result

def NOT(posting):
    result = []
    i = 0
    for item in posting:
        while i < item:
            result.append(i)
            i += 1
        else:
            i += 1
    else:
        while i < no_docs:
            result.append(i)
            i += 1
    return result 

def bool_query(query):
    op=[]
    ans=[i for i in range(no_docs)]
    i=0
    n=len(query)
    while i<len(query):
        if query[i]=='not':
            q = stemm(lemm([query[i+1]]))[0]
            temp=NOT(inv_ind1[q])
            ans=set(ans)
            ans=list(ans.intersection(temp))
            query.remove(query[i])
            query.remove(query[i])
            n-=2
            i-=1
        i+=1
    if len(query)!=0:
        op=[]
        for i in query:
            if i in ["or", "and"]:
               op.append(i)
               query.remove(i)
        query = stemm(lemm(query))
        temp = inv_ind1[query[0]]
        temp=set(temp)
        ans=list(temp.intersection(ans))
        for i in range(len(op)):
            if op[i]=='and':
                ans=AND(ans,inv_ind1[query[i+1]])
            elif op[i]=='or':
                ans=OR(ans,inv_ind1[query[i+1]])
    return ans

### Search for terms in the query and analyse query response time

#### Example 1

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: drugs and violence
[1, 66, 178, 321, 689]
Time taken:  0.0003387770002518664


#### Example 2

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: comedy not family
[2, 3, 544, 548, 51, 61, 576, 577, 589, 89, 91, 94, 610, 101, 614, 106, 621, 634, 122, 638, 140, 657, 151, 663, 155, 156, 157, 679, 690, 180, 693, 703, 704, 708, 198, 199, 207, 210, 723, 724, 734, 228, 229, 751, 762, 259, 773, 266, 783, 785, 278, 791, 305, 829, 837, 326, 844, 360, 363, 364, 366, 881, 370, 882, 374, 886, 888, 890, 904, 905, 907, 403, 918, 922, 417, 931, 421, 947, 439, 963, 460, 973, 464, 976, 980, 475, 476, 480, 487, 488, 505]
Time taken:  0.0006625070000154665


#### Example 3

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: stunning or innovative
[5, 8, 23, 34, 62, 96, 109, 183, 259, 289, 306, 327, 353, 361, 611, 679, 707, 738, 802, 803, 805, 870, 897, 923, 925, 973]
Time taken:  0.0006550489997607656


### Positional postings list

In [ ]:
pos_ind1={}
lines_doc={}
line_no=0
for i in df1['review_new']:
    for pos,item in enumerate(i):
        if item not in pos_ind1:
            pos_ind1[item]=[]
            pos_ind1[item].append(1)
            pos_ind1[item].append({})
            pos_ind1[item][1][line_no]=[pos]
        else:
            pos_ind1[item][0]=pos_ind1[item][0]+1
            if line_no in pos_ind1[item][1]:
                pos_ind1[item][1][line_no].append(pos)
            else:
                pos_ind1[item][1][line_no]=[pos]
    lines_doc[line_no]="In tweet "+str(line_no+1)
    line_no+=1
for key in pos_ind1.keys():
  print(key, ":", pos_ind1[key])

Streaming output truncated to the last 5000 lines.
reprehens : [1, {359: [58]}]
nope : [2, {359: [74], 791: [47]}]
overus : [1, {359: [86]}]
inhuman : [3, {360: [2], 873: [118], 915: [141]}]
unheard : [2, {360: [13], 555: [26]}]
enrag : [1, {360: [18]}]
debas : [1, {360: [28]}]
pilger : [2, {360: [33, 48]}]
travesti : [5, {360: [51], 514: [364], 523: [127], 637: [115], 659: [1]}]
complicit : [1, {360: [60]}]
inact : [1, {360: [61]}]
britain : [4, {360: [66], 403: [124], 500: [70], 832: [122]}]
citizenri : [1, {360: [71]}]
do : [3, {360: [75], 366: [116], 419: [67]}]
rockabilli : [1, {361: [26]}]
lloyd : [5, {361: [29], 371: [92], 381: [25], 939: [143, 157]}]
unemploy : [1, {361: [44]}]
smallest : [2, {361: [90], 731: [62]}]
rosalba : [2, {362: [10, 64]}]
neri : [2, {362: [11, 65]}]
villai : [1, {362: [14]}]
damon : [1, {362: [38]}]
undress : [1, {362: [66]}]
parrot : [1, {362: [68]}]
brawl : [5, {362: [91, 125], 429: [139], 499: [367], 552: [6]}]
terenc : [1, {362: [118]}]
bud : [4, {3

### Support functions to retrieve data from dictionary 

In [ ]:
def phrase_query(s):
    res={}
    for i in s:
        if i not in pos_ind1:
            return []
    postings=[[] for i in s]
    
    for i in range(len(s)):
        pos = pos_ind1[s[i]][1]
        for j in pos.items():
            temp=[]
            temp.append(j[0])
            temp.append(j[1])
            postings[i].append(temp)
        doc_list=[[] for i in s]
        for i in range(len(postings)):
            for j in postings[i]:
                doc_list[i].append(j[0])
    
    common_docs=doc_list[0]
    for i in range(1,len(doc_list)):
        common_docs=set(common_docs)
        common_docs = list(common_docs.intersection(doc_list[i]))

    for i in range(len(postings)):
            postings[i]=[x for x in postings[i] if x[0] in common_docs]
    
    for i in range(len(postings)):
            for j in range(len(postings[i])):
                postings[i][j][1]=[x-i for x in postings[i][j][1]]
    result=[]
    
    def intersectLists(lists):
        if len(lists)==0:
            return []
        lists.sort(key=len)
        return list(reduce(lambda x,y: set(x)&set(y),lists))
    
    for i in range(len(postings[0])):
        li=intersectLists( [x[i][1] for x in postings] )
        if li==[]:
            continue
        else:
            result.append(postings[0][i][0])
    print(f"The phrase was found in the documents: {result}")

### Retrieve data from dictionary and analyse query response time

#### Example 1

In [ ]:
stop_words = set(stopwords.words('english')) 
stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
s=input("Enter the phrase to be searched: ").strip().lower()
start = time.perf_counter()
s=s.split()
for i in range(len(s)):
    if('http' or 'www')in s[i]:
        s[i]=''
    if s[i] in stop_words:
        s[i]=''
s=stemm(lemm(s))
phrase_query(s)
end=time.perf_counter()
print("Time taken: ",end-start)

Enter the phrase to be searched: civil war
The phrase was found in the documents: [29, 198, 238, 334, 549, 710]
Time taken:  0.0014463960005741683


#### Example 2

In [ ]:
stop_words = set(stopwords.words('english')) 
stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
s=input("Enter the phrase to be searched: ").strip().lower()
start = time.perf_counter()
s=s.split()
for i in range(len(s)):
    if('http' or 'www')in s[i]:
        s[i]=''
    if s[i] in stop_words:
        s[i]=''
s=stemm(lemm(s))
phrase_query(s)
end=time.perf_counter()
print("Time taken: ",end-start)

Enter the phrase to be searched: modern day
The phrase was found in the documents: [156, 172, 393, 646, 665, 818, 976]
Time taken:  0.000834644999486045


## Corpus 3 : Medical data

### Extract csv and convert to dataframe

In [ ]:
df2 = pd.read_csv(open('/content/gdrive/MyDrive/medical_data.csv'))
# df2 = pd.read_csv('medical_data.csv')
df2 = df2[:999]
df2 = df2[['description']]
df2.head()

description
0   A 23-year-old white female presents with comp...
1           Consult for laparoscopic gastric bypass.
2           Consult for laparoscopic gastric bypass.
3                             2-D M-Mode. Doppler.  
4                                 2-D Echocardiogram

### Cleaning and Preprocessing data

In [ ]:
df2.shape

(999, 1)

In [ ]:
def tokenize_reg():
    df2['description'] = df2['description'].replace(r'http\S+','',regex=True).replace(r'www\S+','',regex=True).replace(r'Booking.com','',regex=True)
    tokens = RegexpTokenizer(r'\w+')
    df2['description']=df2['description'].apply(lambda x:tokens.tokenize(x.lower()))
    stop_words = set(stopwords.words('english')) 
    stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")

    df2['description'] = df2['description'].apply(lambda x: [item for item in x if item not in stop_words])
tokenize_reg()

In [ ]:
lem = WordNetLemmatizer()
def lemm(text):
    sent=[]
    for word in text:
        sent.append(lem.lemmatize(word))
    return sent

ps=PorterStemmer()

def stemm(text):        
    sent = []
    for word in text:
        sent.append(ps.stem(word))
    return sent

df2['description'] =  df2.apply(lambda x: stemm(lemm(x['description'])), axis=1)

In [ ]:
df2

description
0    [23, year, old, white, femal, present, complai...
1               [consult, laparoscop, gastric, bypass]
2               [consult, laparoscop, gastric, bypass]
3                                   [2, mode, doppler]
4                                  [2, echocardiogram]
..                                                 ...
994  [colonoscopi, due, hematochezia, person, histo...
995  [patient, activ, flare, inflammatori, bowel, d...
996     [colonoscopi, diarrhea, suspect, irrit, bowel]
997  [colonoscopi, evalu, prior, histori, neoplast,...
998  [colonoscopi, biopsi, epinephrin, sclerotherap...

[999 rows x 1 columns]

### Postings list and filling inverted index

In [ ]:
inv_ind2={}
cnt=1
for i in df2['description']:
    for item in i:
        if item not in inv_ind2:
            inv_ind2[item]=[]
        if cnt not in inv_ind2[item]:
            inv_ind2[item].append(cnt)
    cnt+=1
for key in inv_ind2.keys():
  print(key, ":", inv_ind2[key])

23 : [1, 190, 809]
year : [1, 6, 20, 29, 32, 53, 68, 78, 102, 104, 108, 114, 137, 184, 192, 214, 217, 228, 254, 266, 289, 366, 408, 414, 419, 426, 455, 497, 505, 520, 557, 571, 631, 651, 690, 693, 696, 731, 753, 765, 769, 780, 809, 820, 825, 841, 854, 875, 891, 896, 903, 905, 934, 969, 977, 978]
old : [1, 6, 20, 32, 50, 53, 68, 70, 78, 102, 104, 108, 114, 137, 184, 192, 214, 217, 228, 254, 266, 289, 335, 345, 366, 408, 414, 419, 426, 455, 497, 505, 520, 535, 555, 557, 571, 631, 645, 651, 690, 693, 696, 731, 753, 765, 769, 771, 780, 809, 820, 825, 841, 854, 875, 891, 896, 903, 905, 934, 969, 977, 978]
white : [1]
femal : [1, 6, 20, 184, 192, 214, 228, 254, 275, 289, 366, 520, 557, 578, 585, 621, 631, 651, 704, 753, 769, 825, 875, 903, 932, 969, 977]
present : [1, 14, 20, 62, 118, 120, 164, 184, 275, 326, 414, 419, 426, 578, 651, 773, 780, 806, 875, 887, 896, 903, 914, 932]
complaint : [1, 62, 557, 779, 914]
allergi : [1]
consult : [2, 3, 122, 155, 335]
laparoscop : [2, 3, 6, 11, 14, 16,

### Support functions to search for terms in the query

In [ ]:
no_docs=df2.shape[0]

def AND(posting1, posting2):
    pst1 = set(posting1)
    pst2 = set(posting2)
    result = sorted(list(pst1.intersection(pst2)))
    return result

def OR(posting1, posting2):
    pst1 = set(posting1)
    pst2 = set(posting2)
    result = sorted(list(pst1.union(pst2)))
    return result

def NOT(posting):
    result = []
    i = 0
    for item in posting:
        while i < item:
            result.append(i)
            i += 1
        else:
            i += 1
    else:
        while i < no_docs:
            result.append(i)
            i += 1
    return result 

def bool_query(query):
    op=[]
    ans=[i for i in range(no_docs)]
    i=0
    n=len(query)
    while i<len(query):
        if query[i]=='not':
            q = stemm(lemm([query[i+1]]))[0]
            temp=NOT(inv_ind2[q])
            ans=set(ans)
            ans=list(ans.intersection(temp))
            query.remove(query[i])
            query.remove(query[i])
            n-=2
            i-=1
        i+=1
    if len(query)!=0:
        op=[]
        for i in query:
            if i in ["or", "and"]:
               op.append(i)
               query.remove(i)
        query = stemm(lemm(query))
        temp = inv_ind2[query[0]]
        temp=set(temp)
        ans=list(temp.intersection(ans))
        for i in range(len(op)):
            if op[i]=='and':
                ans=AND(ans,inv_ind2[query[i+1]])
            elif op[i]=='or':
                ans=OR(ans,inv_ind2[query[i+1]])
    return ans

### Search for terms in the query and analyse query response time

#### Example 1

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: lungs or neck or liver
[17, 27, 60, 171, 246, 288, 338, 360, 488, 525, 528, 549, 594, 601, 614, 633, 707, 800, 804, 805, 818]
Time taken:  0.0003875070005960879


#### Example 2

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: heart not cancer
[262, 12, 909, 284, 192, 584, 587, 588, 971, 978, 736, 739, 740, 743, 744, 745, 746, 747, 748, 749, 750, 751, 752, 753, 754, 755, 756, 757, 760, 764, 765]
Time taken:  0.0007460609995177947


#### Example 3

In [ ]:
query = input("Enter your query: ").strip().split()
start=time.perf_counter()
print(bool_query(query))
end=time.perf_counter()
print("Time taken: ",end-start)

Enter your query: history and cancer
[520, 805]
Time taken:  0.0003782540006795898


### Positional postings list

In [ ]:
pos_ind2={}
lines_doc={}
line_no=0
for i in df2['description']:
    for pos,item in enumerate(i):
        if item not in pos_ind2:
            pos_ind2[item]=[]
            pos_ind2[item].append(1)
            pos_ind2[item].append({})
            pos_ind2[item][1][line_no]=[pos]
        else:
            pos_ind2[item][0]=pos_ind2[item][0]+1
            if line_no in pos_ind2[item][1]:
                pos_ind2[item][1][line_no].append(pos)
            else:
                pos_ind2[item][1][line_no]=[pos]
    lines_doc[line_no]="In tweet "+str(line_no+1)
    line_no+=1
for key in pos_ind2.keys():
  print(key, ":", pos_ind2[key])

23 : [3, {0: [0], 189: [5], 808: [19]}]
year : [60, {0: [1], 5: [12, 17], 19: [2], 28: [2, 8], 31: [1], 52: [1], 67: [6], 77: [3], 101: [1], 103: [9], 107: [10], 113: [3], 136: [11], 183: [6], 191: [5], 213: [1], 216: [7], 227: [6], 253: [11, 18], 265: [6], 288: [8], 365: [9], 407: [2], 413: [14], 418: [8], 425: [1], 454: [1], 496: [3], 504: [10], 519: [8], 556: [8], 570: [4], 630: [12, 17], 650: [4], 689: [9], 692: [1], 695: [10], 730: [3], 752: [13], 764: [9], 768: [7], 779: [8], 808: [20], 819: [7], 824: [10], 840: [3], 853: [6], 874: [4], 890: [13], 895: [9], 902: [1], 904: [2], 933: [11], 968: [11], 976: [4], 977: [3]}]
old : [63, {0: [2], 5: [13], 19: [3], 31: [2], 49: [2], 52: [2], 67: [7], 69: [3], 77: [4], 101: [2], 103: [10], 107: [11], 113: [4], 136: [12], 183: [7], 191: [6], 213: [2], 216: [8], 227: [7], 253: [12], 265: [7], 288: [9], 334: [6], 344: [6], 365: [10], 407: [3], 413: [15], 418: [9], 425: [2], 454: [2], 496: [4], 504: [11], 519: [9], 534: [1], 554: [9], 556: [9]

### Support functions to retrieve data from dictionary 

In [ ]:
def phrase_query(s):
    res={}
    for i in s:
        if i not in pos_ind2:
            return []
    postings=[[] for i in s]
    
    for i in range(len(s)):
        pos = pos_ind2[s[i]][1]
        for j in pos.items():
            temp=[]
            temp.append(j[0])
            temp.append(j[1])
            postings[i].append(temp)
        doc_list=[[] for i in s]
        for i in range(len(postings)):
            for j in postings[i]:
                doc_list[i].append(j[0])
    
    common_docs=doc_list[0]
    for i in range(1,len(doc_list)):
        common_docs=set(common_docs)
        common_docs = list(common_docs.intersection(doc_list[i]))

    for i in range(len(postings)):
            postings[i]=[x for x in postings[i] if x[0] in common_docs]
    
    for i in range(len(postings)):
            for j in range(len(postings[i])):
                postings[i][j][1]=[x-i for x in postings[i][j][1]]
    result=[]
    
    def intersectLists(lists):
        if len(lists)==0:
            return []
        lists.sort(key=len)
        return list(reduce(lambda x,y: set(x)&set(y),lists))
    
    for i in range(len(postings[0])):
        li=intersectLists( [x[i][1] for x in postings] )
        if li==[]:
            continue
        else:
            result.append(postings[0][i][0])
    print(f"The phrase was found in the documents: {result}")

### Retrieve data from dictionary and analyse query response time

#### Example 1

In [ ]:
stop_words = set(stopwords.words('english')) 
stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
s=input("Enter the phrase to be searched: ").strip().lower()
start = time.perf_counter()
s=s.split()
for i in range(len(s)):
    if('http' or 'www')in s[i]:
        s[i]=''
    if s[i] in stop_words:
        s[i]=''
s=stemm(lemm(s))
phrase_query(s)
end=time.perf_counter()
print("Time taken: ",end-start)

Enter the phrase to be searched: pulmonary valve
The phrase was found in the documents: [398]
Time taken:  0.0010455080000610906


#### Example 2

In [ ]:
stop_words = set(stopwords.words('english')) 
stop_words = stop_words.union(",","(",")","[","]","{","}","#","@","!",":",";",".","?")
s=input("Enter the phrase to be searched: ").strip().lower()
start = time.perf_counter()
s=s.split()
for i in range(len(s)):
    if('http' or 'www')in s[i]:
        s[i]=''
    if s[i] in stop_words:
        s[i]=''
s=stemm(lemm(s))
phrase_query(s)
end=time.perf_counter()
print("Time taken: ",end-start)

Enter the phrase to be searched: emergency room
The phrase was found in the documents: [19, 469]
Time taken:  0.00043573400034802034
